In [1]:
import numpy as np 
import pandas 
from itertools import product, combinations
from primer3 import calcHomodimer, calcHeterodimer, calcTm

In [2]:
# generate all possible 8-mer DNA sequences without homopolymers
# we want to avoid homopolyers in our barcodes 

In [3]:
alphabet = 'ATCG'

In [4]:
def has_homopolymers( sequence ):
    for i in range( len( sequence ) - 1 ):
        if sequence[ i ] == sequence[ i + 1 ]:
            return True 
    return False

In [5]:
barcode_length = 8 
barcodes = []
for combo in product( alphabet, repeat=barcode_length ):
    if not has_homopolymers( combo ):
        barcodes.append( ''.join( combo ) )

In [6]:
# primer sequences for our test run are 
# T7 (forward): 5'-TAATACGACTCACTATAGGG-3'
# T7term (reverse): 5'-GCTAGTTATTGCTCAGCGG-3'
# we will add barcodes to the 5' end of both primers 
# assume the Tm of the T7 primers is good as is

In [7]:
# calculate the propensity of the primers to dimerize 

In [8]:
# so this works for generic Sanger primer, 
# we make these variables 

In [9]:
forward_sanger_primer = 'TAATACGACTCACTATAGGG'
reverse_sanger_primer = 'GCTAGTTATTGCTCAGCGG'

In [10]:
# describe the input primers 

forward_seq_primer_tm = calcTm( forward_sanger_primer ) 
reverse_seq_primer_tm = calcTm( reverse_sanger_primer ) 

print( '{0:2.2f}, {1:2.2f}'.format( forward_seq_primer_tm, reverse_seq_primer_tm ) )

wt_tm = { 'forward': forward_seq_primer_tm, 'reverse': reverse_seq_primer_tm } 

44.59, 50.61


In [11]:
fwd_primers = [ b + forward_sanger_primer for b in barcodes ]
rev_primers = [ b + reverse_sanger_primer for b in barcodes ]

In [12]:
# let's make a DataFrame out of this right now 
data = [ ( fwd_primer, 'forward' ) for fwd_primer in fwd_primers ] + [ ( rev_primer, 'reverse' ) for rev_primer in rev_primers ] 
df = pandas.DataFrame( data, columns=['sequence', 'direction'] )
df.sample( 2 ) 

sequence direction
10914   AGCGCAGAGCTAGTTATTGCTCAGCGG   reverse
5995   CGAGATACTAATACGACTCACTATAGGG   forward

In [13]:
# calc Tm for each 

df[ 'primary_tm' ] = list( map( lambda x: wt_tm[x], df.direction ) ) 
df[ 'secondary_tm' ] = list( map( calcTm, df.sequence ) ) 
df.sample( 2 ) 

sequence direction  primary_tm  secondary_tm
1202  ACTGCTCGTAATACGACTCACTATAGGG   forward   44.591869     57.395174
5228  CTACTCGCTAATACGACTCACTATAGGG   forward   44.591869     55.807218

In [14]:
# exclude homodimers 

df[ 'homodimer' ] = list( map( lambda x: calcHomodimer( x ).structure_found, df.sequence ) )
df.sample( 2 ) 

# fwd_primers = list( filter( lambda x: calcHomodimer( x ).structure_found, fwd_primers ) ) 
# rev_primers = list( filter( lambda x: calcHomodimer( x ).structure_found, rev_primers ) ) 
# print( len( fwd_primers) )
# print( len( rev_primers) )
# I guess there are none 

sequence direction  primary_tm  secondary_tm  \
13531   CACGATCTGCTAGTTATTGCTCAGCGG   reverse   50.612736     59.814901   
3498   TCGTACGATAATACGACTCACTATAGGG   forward   44.591869     55.340463   

      homodimer  
13531      True  
3498       True

In [15]:
# so, now let's filter this list down 

# first, let's exclude the homopolymers we accidentally introduced 
# that arise because the barcode is next to the sequencing primer 
# remove these homopolymers 

# second, calculate the secondary Tm (Tm of entire barcode+primer pair) 
# throw out if the secondary Tm is too far from the original Tm
# is there a way to set up the PCR that will work for a wide variety of Tm? 

# third, of all of the primers that pass, form a pool and calculate the propensity 
# of hetreodimeriztion pairwise until they are pairwise independent

# only then think about Hamming distances
# I'm guessing 100 

In [16]:
def check_introduced_homopolymers( sequence, barcode_length ):
    # barcode is on the 5' end of the sequence
    if sequence[ barcode_length ] == sequence[ barcode_length - 1 ]:
        return True 
    else:
        return False 
    
df[ 'introduced_homopolymers' ] = df.sequence.map( lambda x: check_introduced_homopolymers( x, barcode_length ) )
df.sample( 2 ) 

sequence direction  primary_tm  secondary_tm  \
11309  TACTCGTGGCTAGTTATTGCTCAGCGG   reverse   50.612736     60.379057   
14482  CTGTGTACGCTAGTTATTGCTCAGCGG   reverse   50.612736     59.764682   

      homodimer introduced_homopolymers  
11309      True                    True  
14482      True                   False

In [17]:
pandas.options.display.max_rows = 10000
df

sequence direction  primary_tm  secondary_tm  \
0      ATATATATTAATACGACTCACTATAGGG   forward   44.591869     48.022858   
1      ATATATACTAATACGACTCACTATAGGG   forward   44.591869     49.328667   
2      ATATATAGTAATACGACTCACTATAGGG   forward   44.591869     49.328667   
3      ATATATCATAATACGACTCACTATAGGG   forward   44.591869     49.802981   
4      ATATATCTTAATACGACTCACTATAGGG   forward   44.591869     49.753013   
5      ATATATCGTAATACGACTCACTATAGGG   forward   44.591869     51.642664   
6      ATATATGATAATACGACTCACTATAGGG   forward   44.591869     49.802981   
7      ATATATGTTAATACGACTCACTATAGGG   forward   44.591869     50.194966   
8      ATATATGCTAATACGACTCACTATAGGG   forward   44.591869     51.799411   
9      ATATACATTAATACGACTCACTATAGGG   forward   44.591869     50.194966   
10     ATATACACTAATACGACTCACTATAGGG   forward   44.591869     51.491256   
11     ATATACAGTAATACGACTCACTATAGGG   forward   44.591869     51.491256   
12     ATATACTATAATACGACTCACTATAGGG   forward   44.591869     49.328667   
13     ATATACTCTAATACGACTCACTATAGGG   forward   44.591869     51.053656   
14     ATATACTGTAATACGACTCACTATAGGG   forward   44.591869     51.491256   
15     ATATACGATAATACGACTCACTATAGGG   forward   44.591869     51.642664   
16     ATATACGTTAATACGACTCACTATAGGG   forward   44.591869     52.025138   
17     ATATACGCTAATACGACTCACTATAGGG   forward   44.591869     53.611441   
18     ATATAGATTAATACGACTCACTATAGGG   forward   44.591869     49.753013   
19     ATATAGACTAATACGACTCACTATAGGG   forward   44.591869     51.053656   
20     ATATAGAGTAATACGACTCACTATAGGG   forward   44.591869     51.053656   
21     ATATAGTATAATACGACTCACTATAGGG   forward   44.591869     49.328667   
22     ATATAGTCTAATACGACTCACTATAGGG   forward   44.591869     51.053656   
23     ATATAGTGTAATACGACTCACTATAGGG   forward   44.591869     51.491256   
24     ATATAGCATAATACGACTCACTATAGGG   forward   44.591869     51.799411   
25     ATATAGCTTAATACGACTCACTATAGGG   forward   44.591869     51.749352   
26     ATATAGCGTAATACGACTCACTATAGGG   forward   44.591869     53.611441   
27     ATATCATATAATACGACTCACTATAGGG   forward   44.591869     49.802981   
28     ATATCATCTAATACGACTCACTATAGGG   forward   44.591869     51.525273   
29     ATATCATGTAATACGACTCACTATAGGG   forward   44.591869     51.961090   
30     ATATCACATAATACGACTCACTATAGGG   forward   44.591869     51.961090   
31     ATATCACTTAATACGACTCACTATAGGG   forward   44.591869     51.911052   
32     ATATCACGTAATACGACTCACTATAGGG   forward   44.591869     53.769861   
33     ATATCAGATAATACGACTCACTATAGGG   forward   44.591869     51.525273   
34     ATATCAGTTAATACGACTCACTATAGGG   forward   44.591869     51.911052   
35     ATATCAGCTAATACGACTCACTATAGGG   forward   44.591869     53.509688   
36     ATATCTATTAATACGACTCACTATAGGG   forward   44.591869     49.753013   
37     ATATCTACTAATACGACTCACTATAGGG   forward   44.591869     51.053656   
38     ATATCTAGTAATACGACTCACTATAGGG   forward   44.591869     51.053656   
39     ATATCTCATAATACGACTCACTATAGGG   forward   44.591869     51.525273   
40     ATATCTCTTAATACGACTCACTATAGGG   forward   44.591869     51.475156   
41     ATATCTCGTAATACGACTCACTATAGGG   forward   44.591869     53.343627   
42     ATATCTGATAATACGACTCACTATAGGG   forward   44.591869     51.525273   
43     ATATCTGTTAATACGACTCACTATAGGG   forward   44.591869     51.911052   
44     ATATCTGCTAATACGACTCACTATAGGG   forward   44.591869     53.509688   
45     ATATCGATTAATACGACTCACTATAGGG   forward   44.591869     52.059920   
46     ATATCGACTAATACGACTCACTATAGGG   forward   44.591869     53.343627   
47     ATATCGAGTAATACGACTCACTATAGGG   forward   44.591869     53.343627   
48     ATATCGTATAATACGACTCACTATAGGG   forward   44.591869     51.642664   
49     ATATCGTCTAATACGACTCACTATAGGG   forward   44.591869     53.343627   
50     ATATCGTGTAATACGACTCACTATAGGG   forward   44.591869     53.769861   
51     ATATCGCATAATACGACTCACTATAGGG   forward   44.591869     54.074681   
52     ATATCGCTTAATACGACTCACTATAGGG   forward   44.5